In [28]:
from IPython.core.interactiveshell import InteractiveShell
InteractiveShell.ast_node_interactivity = "all" 

In [1]:
import sys
import os

sys.path.append(os.path.abspath("../")) 

In [ ]:
import pandas as pd
import numpy as np
import json
import xgboost as xgb
import matplotlib.pyplot as plt
from sklearn.metrics import mean_squared_error, mean_absolute_percentage_error
from sklearn.model_selection import train_test_split
from src.metric_logging import log_experiment

In [27]:
# Load merged dataset
file_path = "../datasets/final_merged_dataset.parquet"
merged_data = pd.read_parquet(file_path)

# Ensure 'date' column is in datetime format
merged_data['date'] = pd.to_datetime(merged_data['date'])
merged_data.set_index('date', inplace=True)

# Select structured features: Bitcoin Price, Sentiment, and Volume
feature_columns = ['Close', 'Open', 'High', 'Low', 'Volume', 'sentiment_score', 'bert_sentiment']
data = merged_data[feature_columns]

# Drop NaN values
data.dropna(inplace=True)

/var/folders/x5/7fmrypvd2mj6rc45kq6kv2lh0000gn/T/ipykernel_13188/2768040244.py:14: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  data.dropna(inplace=True)


In [32]:
data.head()
data.shape

Close      Open      High       Low    Volume  sentiment_score  \
date                                                                            
2021-01-01  0.262398  0.255213  0.254063  0.260019  0.096184              0.0   
2021-01-02  0.315568  0.262601  0.321720  0.265682  0.175237              0.0   
2021-01-03  0.328213  0.315780  0.349385  0.323992  0.206700              0.0   
2021-01-04  0.312568  0.328945  0.327147  0.258427  0.213978              0.0   
2021-01-05  0.351590  0.312836  0.346131  0.287934  0.174310              0.0   

            bert_sentiment  
date                        
2021-01-01             0.0  
2021-01-02             0.0  
2021-01-03             0.0  
2021-01-04             0.0  
2021-01-05             0.0

(761, 7)

In [45]:
# Create lag features (past N days as features)
N = 5  # Lookback window
for i in range(1, N+1):
    data[f'Close_lag_{i}'] = data['Close'].shift(i)

# Create rolling averages
data['rolling_avg_7'] = data['Close'].rolling(window=7).mean()
data['rolling_avg_14'] = data['Close'].rolling(window=14).mean()
data['rolling_avg_30'] = data['Close'].rolling(window=30).mean()

# Bollinger Bands (Volatility Measure)
data['bollinger_high'] = data['rolling_avg_14'] + (2 * data['Close'].rolling(window=14).std())
data['bollinger_low'] = data['rolling_avg_14'] - (2 * data['Close'].rolling(window=14).std())

# Drop NaN values after feature creation
data.dropna(inplace=True)

In [36]:
data.head()
data.shape

Close      Open      High       Low    Volume  sentiment_score  \
date                                                                            
2021-01-30  0.356941  0.357631  0.353690  0.341475  0.167302              0.0   
2021-01-31  0.334632  0.357147  0.343290  0.328282  0.131214              0.0   
2021-02-01  0.342797  0.334810  0.349950  0.330527  0.156402              0.0   
2021-02-02  0.380903  0.342897  0.373908  0.352287  0.161321              0.0   
2021-02-03  0.418791  0.381099  0.404045  0.390779  0.155722              0.0   

            bert_sentiment  Close_lag_1  Close_lag_2  Close_lag_3  \
date                                                                
2021-01-30             0.0     0.357846     0.341425     0.282839   
2021-01-31             0.0     0.356941     0.357846     0.341425   
2021-02-01             0.0     0.334632     0.356941     0.357846   
2021-02-02             0.0     0.342797     0.334632     0.356941   
2021-02-03             0.0     0.380903     0.342797     0.334632   

            Close_lag_4  Close_lag_5  rolling_avg_7  rolling_avg_14  \
date                                                                  
2021-01-30     0.324116     0.320186       0.328865        0.342974   
2021-01-31     0.282839     0.324116       0.331141        0.339281   
2021-02-01     0.341425     0.282839       0.334371        0.335014   
2021-02-02     0.357846     0.341425       0.342483        0.334242   
2021-02-03     0.356941     0.357846       0.361905        0.336897   

            rolling_avg_30  bollinger_high  bollinger_low  
date                                                       
2021-01-30        0.367506        0.418380       0.267567  
2021-01-31        0.369913        0.410488       0.268074  
2021-02-01        0.370821        0.396373       0.273655  
2021-02-02        0.372577        0.392734       0.275751  
2021-02-03        0.376118        0.406894       0.266900

(732, 17)

In [46]:
# Define input features (X) and target variable (y)
X = data.drop(columns=['Close'])  # Features
y = data['Close'].shift(-1)  # Shifted to predict next day's close price

# Drop last row from both X and y to maintain equal length
X = X.iloc[:-1]  # Remove last row from X
y = y.dropna()  # Drop NaN row from y

# Print new shapes
print(f"Fixed X shape: {X.shape}, Fixed y shape: {y.shape}")

Fixed X shape: (702, 16), Fixed y shape: (702,)


In [47]:
X.head()
X.shape
y.head()
y.shape

Open      High       Low    Volume  sentiment_score  \
date                                                                  
2021-02-28  0.587468  0.579851  0.544327  0.133223         0.133245   
2021-03-01  0.567484  0.638240  0.581219  0.134526         0.000000   
2021-03-02  0.653496  0.644779  0.622842  0.115996         0.000000   
2021-03-03  0.630387  0.690606  0.643429  0.132573         0.000000   
2021-03-04  0.671078  0.675378  0.631272  0.130018         0.000000   

            bert_sentiment  Close_lag_1  Close_lag_2  Close_lag_3  \
date                                                                
2021-02-28        0.607697     0.587127     0.590049     0.604613   
2021-03-01        0.000000     0.566836     0.587127     0.590049   
2021-03-02        0.000000     0.653616     0.566836     0.587127   
2021-03-03        0.000000     0.629432     0.653616     0.566836   
2021-03-04        0.000000     0.671133     0.629432     0.653616   

            Close_lag_4  Close_lag_5  rolling_avg_7  rolling_avg_14  \
date                                                                  
2021-02-28     0.655047     0.638035       0.626243        0.671771   
2021-03-01     0.604613     0.655047       0.613618        0.674097   
2021-03-02     0.590049     0.604613       0.612389        0.672965   
2021-03-03     0.587127     0.590049       0.614687        0.670743   
2021-03-04     0.566836     0.587127       0.618735        0.666441   

            rolling_avg_30  bollinger_high  bollinger_low  
date                                                       
2021-02-28        0.573171        0.829085       0.514458  
2021-03-01        0.583060        0.829127       0.519068  
2021-03-02        0.592887        0.829128       0.516802  
2021-03-03        0.603831        0.825995       0.515492  
2021-03-04        0.612233        0.822351       0.510531

(702, 16)

date
2021-02-28    0.653616
2021-03-01    0.629432
2021-03-02    0.671133
2021-03-03    0.632950
2021-03-04    0.640021
Name: Close, dtype: float64

(702,)

In [48]:
# Split 80% Train, 20% Test
train_size = int(len(data) * 0.8)
X_train, X_test = X.iloc[:train_size], X.iloc[train_size:]
y_train, y_test = y.iloc[:train_size], y.iloc[train_size:]

# Print dataset sizes
print(f"Train Size: {len(X_train)}, Test Size: {len(X_test)}")

Train Size: 562, Test Size: 140


In [49]:
print(f"X_test index range: {X_test.index.min()} to {X_test.index.max()}")
print(f"y_test index range: {y_test.index.min()} to {y_test.index.max()}")

X_test index range: 2022-09-13 00:00:00 to 2023-01-30 00:00:00
y_test index range: 2022-09-13 00:00:00 to 2023-01-30 00:00:00


In [50]:
X_train_np, X_test_np = X_train.to_numpy(), X_test.to_numpy()
y_train_np, y_test_np = y_train.to_numpy(), y_test.to_numpy()
print(f"X_train shape: {X_train_np.shape}, y_train shape: {y_train_np.shape}")
print(f"X_test shape: {X_test_np.shape}, y_test shape: {y_test_np.shape}")

X_train shape: (562, 16), y_train shape: (562,)
X_test shape: (140, 16), y_test shape: (140,)


In [51]:
import xgboost as xgb
from sklearn.metrics import mean_squared_error
import numpy as np

# Ensure input data is in NumPy format
X_train_np, X_test_np = X_train.to_numpy(), X_test.to_numpy()
y_train_np, y_test_np = y_train.to_numpy(), y_test.to_numpy()

# Define XGBoost model
xgb_model = xgb.XGBRegressor(
    objective='reg:squarederror', 
    n_estimators=500,  
    learning_rate=0.05,  
    max_depth=6,  
    subsample=0.8,
    colsample_bytree=0.8,
    random_state=42
)

# Train XGBoost with manual early stopping
min_rmse = float("inf")
best_iteration = 0
tolerance = 50  # Same as early_stopping_rounds=50
rmse_history = []

for n in range(1, 501):  # Loop through each boosting round
    xgb_model.set_params(n_estimators=n)  # Update model with current round
    xgb_model.fit(X_train_np, y_train_np)  # Train model
    
    # Predict on test set
    y_pred = xgb_model.predict(X_test_np)
    
    # Compute RMSE
    rmse = np.sqrt(mean_squared_error(y_test_np, y_pred))
    rmse_history.append(rmse)

    print(f"Iteration {n}, RMSE: {rmse:.4f}")

    # Early stopping condition
    if rmse < min_rmse:
        min_rmse = rmse
        best_iteration = n  # Store best iteration
    elif n - best_iteration >= tolerance:
        print(f"Stopping early at iteration {n}. Best RMSE: {min_rmse:.4f}")
        break  # Stop training if no improvement for 50 rounds

XGBRegressor(base_score=None, booster=None, callbacks=None,
             colsample_bylevel=None, colsample_bynode=None,
             colsample_bytree=0.8, device=None, early_stopping_rounds=None,
             enable_categorical=False, eval_metric=None, feature_types=None,
             feature_weights=None, gamma=None, grow_policy=None,
             importance_type=None, interaction_constraints=None,
             learning_rate=0.05, max_bin=None, max_cat_threshold=None,
             max_cat_to_onehot=None, max_delta_step=None, max_depth=6,
             max_leaves=None, min_child_weight=None, missing=nan,
             monotone_constraints=None, multi_strategy=None, n_estimators=1,
             n_jobs=None, num_parallel_tree=None, ...)

XGBRegressor(base_score=None, booster=None, callbacks=None,
             colsample_bylevel=None, colsample_bynode=None,
             colsample_bytree=0.8, device=None, early_stopping_rounds=None,
             enable_categorical=False, eval_metric=None, feature_types=None,
             feature_weights=None, gamma=None, grow_policy=None,
             importance_type=None, interaction_constraints=None,
             learning_rate=0.05, max_bin=None, max_cat_threshold=None,
             max_cat_to_onehot=None, max_delta_step=None, max_depth=6,
             max_leaves=None, min_child_weight=None, missing=nan,
             monotone_constraints=None, multi_strategy=None, n_estimators=1,
             n_jobs=None, num_parallel_tree=None, ...)

Iteration 1, RMSE: 0.4202


XGBRegressor(base_score=None, booster=None, callbacks=None,
             colsample_bylevel=None, colsample_bynode=None,
             colsample_bytree=0.8, device=None, early_stopping_rounds=None,
             enable_categorical=False, eval_metric=None, feature_types=None,
             feature_weights=None, gamma=None, grow_policy=None,
             importance_type=None, interaction_constraints=None,
             learning_rate=0.05, max_bin=None, max_cat_threshold=None,
             max_cat_to_onehot=None, max_delta_step=None, max_depth=6,
             max_leaves=None, min_child_weight=None, missing=nan,
             monotone_constraints=None, multi_strategy=None, n_estimators=2,
             n_jobs=None, num_parallel_tree=None, ...)

XGBRegressor(base_score=None, booster=None, callbacks=None,
             colsample_bylevel=None, colsample_bynode=None,
             colsample_bytree=0.8, device=None, early_stopping_rounds=None,
             enable_categorical=False, eval_metric=None, feature_types=None,
             feature_weights=None, gamma=None, grow_policy=None,
             importance_type=None, interaction_constraints=None,
             learning_rate=0.05, max_bin=None, max_cat_threshold=None,
             max_cat_to_onehot=None, max_delta_step=None, max_depth=6,
             max_leaves=None, min_child_weight=None, missing=nan,
             monotone_constraints=None, multi_strategy=None, n_estimators=2,
             n_jobs=None, num_parallel_tree=None, ...)

...

XGBRegressor(base_score=None, booster=None, callbacks=None,
             colsample_bylevel=None, colsample_bynode=None,
             colsample_bytree=0.8, device=None, early_stopping_rounds=None,
             enable_categorical=False, eval_metric=None, feature_types=None,
             feature_weights=None, gamma=None, grow_policy=None,
             importance_type=None, interaction_constraints=None,
             learning_rate=0.05, max_bin=None, max_cat_threshold=None,
             max_cat_to_onehot=None, max_delta_step=None, max_depth=6,
             max_leaves=None, min_child_weight=None, missing=nan,
             monotone_constraints=None, multi_strategy=None, n_estimators=237,
             n_jobs=None, num_parallel_tree=None, ...)

Iteration 237, RMSE: 0.0676


XGBRegressor(base_score=None, booster=None, callbacks=None,
             colsample_bylevel=None, colsample_bynode=None,
             colsample_bytree=0.8, device=None, early_stopping_rounds=None,
             enable_categorical=False, eval_metric=None, feature_types=None,
             feature_weights=None, gamma=None, grow_policy=None,
             importance_type=None, interaction_constraints=None,
             learning_rate=0.05, max_bin=None, max_cat_threshold=None,
             max_cat_to_onehot=None, max_delta_step=None, max_depth=6,
             max_leaves=None, min_child_weight=None, missing=nan,
             monotone_constraints=None, multi_strategy=None, n_estimators=238,
             n_jobs=None, num_parallel_tree=None, ...)

XGBRegressor(base_score=None, booster=None, callbacks=None,
             colsample_bylevel=None, colsample_bynode=None,
             colsample_bytree=0.8, device=None, early_stopping_rounds=None,
             enable_categorical=False, eval_metric=None, feature_types=None,
             feature_weights=None, gamma=None, grow_policy=None,
             importance_type=None, interaction_constraints=None,
             learning_rate=0.05, max_bin=None, max_cat_threshold=None,
             max_cat_to_onehot=None, max_delta_step=None, max_depth=6,
             max_leaves=None, min_child_weight=None, missing=nan,
             monotone_constraints=None, multi_strategy=None, n_estimators=238,
             n_jobs=None, num_parallel_tree=None, ...)

Iteration 238, RMSE: 0.0676
Stopping early at iteration 238. Best RMSE: 0.0676


In [52]:
# Predict closing prices
y_pred = xgb_model.predict(X_test)

# Create DataFrame for evaluation
predictions_df = pd.DataFrame({
    "Actual_Close": y_test.values,
    "Predicted_Close": y_pred
}, index=y_test.index)

# Forecast for 7-day and 30-day using rolling predictions
predictions_df['Predicted_7d'] = predictions_df['Predicted_Close'].shift(-7)
predictions_df['Predicted_30d'] = predictions_df['Predicted_Close'].shift(-30)

print("✅ XGBoost Predictions completed successfully!")

✅ XGBoost Predictions completed successfully!


In [53]:
# Compute RMSE & MAPE for different forecasting horizons
rmse_1d = np.sqrt(mean_squared_error(predictions_df['Actual_Close'], predictions_df['Predicted_Close']))
rmse_7d = np.sqrt(mean_squared_error(predictions_df['Actual_Close'].iloc[:-7], predictions_df['Predicted_7d'].dropna()))
rmse_30d = np.sqrt(mean_squared_error(predictions_df['Actual_Close'].iloc[:-30], predictions_df['Predicted_30d'].dropna()))

# Compute MAPE
mape_1d = np.mean(np.abs((predictions_df['Actual_Close'] - predictions_df['Predicted_Close']) / predictions_df['Actual_Close'])) * 100
mape_7d = np.mean(np.abs((predictions_df['Actual_Close'].iloc[:-7] - predictions_df['Predicted_7d'].dropna()) / predictions_df['Actual_Close'].iloc[:-7])) * 100
mape_30d = np.mean(np.abs((predictions_df['Actual_Close'].iloc[:-30] - predictions_df['Predicted_30d'].dropna()) / predictions_df['Actual_Close'].iloc[:-30])) * 100

# Print Evaluation Results
print(f"✅ XGBoost Model Evaluation:")
print(f"RMSE (1-day): {rmse_1d:.4f}, MAPE (1-day): {mape_1d:.2f}%")
print(f"RMSE (7-day): {rmse_7d:.4f}, MAPE (7-day): {mape_7d:.2f}%")
print(f"RMSE (30-day): {rmse_30d:.4f}, MAPE (30-day): {mape_30d:.2f}%")

✅ XGBoost Model Evaluation:
RMSE (1-day): 0.0676, MAPE (1-day): inf%
RMSE (7-day): 0.0706, MAPE (7-day): inf%
RMSE (30-day): 0.0759, MAPE (30-day): inf%


In [54]:
# Prepare metrics for logging
xgb_metrics = {
    "RMSE": rmse_1d,
    "RMSE_7d": rmse_7d,
    "RMSE_30d": rmse_30d
}

# Log results to MLflow
log_experiment("XGBoost", {}, xgb_metrics)

print("✅ XGBoost RMSE logged successfully to DagsHub MLflow!")

jai_balayya
✅ XGBoost metrics logged successfully to DagsHub MLflow.
🏃 View run XGBoost-Baseline at: https://dagshub.com/vamsisaigarapati/bitcoin_price_pred_CSE574.mlflow/#/experiments/0/runs/500c75cca2f1444ca1c09606fc2968f4
🧪 View experiment at: https://dagshub.com/vamsisaigarapati/bitcoin_price_pred_CSE574.mlflow/#/experiments/0
✅ XGBoost RMSE logged successfully to DagsHub MLflow!
